In [2]:
import os
import cv2
import numpy as np

In [3]:
def downsample_video(input_video_path, output_video_path, temporal_factor=1, spatial_factor=1):
    """
    Downsamples a video either temporally (by frame rate) or spatially (by resolution).
    
    Parameters:
    - input_video_path: Path to the input video file.
    - output_video_path: Path to save the downsampled video.
    - temporal_factor: Factor to downsample temporally (e.g., 2 means keeping every 2nd frame).
    - spatial_factor: Factor to downsample spatially (e.g., 2 means resizing each frame to half the original size).
    
    Returns:
    - None (saves the downsampled video to the specified output path).
    """
    
    # Open the input video
    cap = cv2.VideoCapture(input_video_path)
    
    # Get video properties
    fps = cap.get(cv2.CAP_PROP_FPS)
    width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    
    # Calculate the downsampled video dimensions
    new_width = int(width / spatial_factor)
    new_height = int(height / spatial_factor)
    
    # Create VideoWriter to save the downsampled video
    fourcc = cv2.VideoWriter_fourcc(*'XVID')  # You can use other codecs if needed
    out = cv2.VideoWriter(output_video_path, fourcc, fps, (new_width, new_height))
    
    # Read and process the frames
    frame_count = 0
    while True:
        ret, frame = cap.read()
        if not ret:
            break
        # Downsample temporally (skip frames based on temporal_factor)
        if frame_count % temporal_factor == 0:
            # Resize the frame for spatial downsampling
            resized_frame = cv2.resize(frame, (new_width, new_height))
            # Write the downsampled frame to the output video
            out.write(resized_frame)
        frame_count += 1

    # Release resources
    cap.release()
    out.release()
    
    print(f"Downsampled video saved to {output_video_path}")

def extract_frames_from_video(video_path, output_folder):
    # Open the video file
    cap = cv2.VideoCapture(video_path)
    
    # Check if the video file was opened correctly
    if not cap.isOpened():
        print("Error: Couldn't open video.")
        return
    
    # Create output folder if it doesn't exist
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    
    frame_count = 0
    while True:
        ret, frame = cap.read()
        if not ret:
            break
        
        # Save frame as image
        frame_filename = os.path.join(output_folder, f"frame_{frame_count:04d}.jpg")
        cv2.imwrite(frame_filename, frame)
        
        frame_count += 1

    cap.release()
    print(f"Extracted {frame_count} frames to {output_folder}")

In [4]:
# usage
cur_dir = os.getcwd()
data_dir = "data/NeRF_example.mp4"
data_path = os.path.join(cur_dir, data_dir)
processed_data_path = os.path.join(cur_dir, "processed_data")
frame_output = os.path.join(cur_dir, "data/frames")
extract_frames_from_video(data_path, frame_output)

Extracted 1041 frames to /home/sameer/Documents/MP_Projects/MP_Project_2/data/frames


In [5]:
# run preprocessing of video/image data
data_type = "images" # video or image
os.system(f"ns-process-data {data_type} --data {frame_output} --output-dir {processed_data_path}")

[16:08:42] 🎉 Done copying images with prefix 'frame_'.                                        ]8;id=377923;file:///home/sameer/miniconda3/envs/nerf/lib/python3.10/site-packages/nerfstudio/process_data/process_data_utils.py\process_data_utils.py]8;;\:]8;id=658760;file:///home/sameer/miniconda3/envs/nerf/lib/python3.10/site-packages/nerfstudio/process_data/process_data_utils.py#340\340]8;;\
(   ●  ) Copying images...
🌖  Running COLMAP feature extractor...tor...
[16:08:49] 🎉 Done extracting COLMAP features.                                                       ]8;id=818792;file:///home/sameer/miniconda3/envs/nerf/lib/python3.10/site-packages/nerfstudio/process_data/colmap_utils.py\colmap_utils.py]8;;\:]8;id=248916;file:///home/sameer/miniconda3/envs/nerf/lib/python3.10/site-packages/nerfstudio/process_data/colmap_utils.py#137\137]8;;\
🚶  Running COLMAP feature matcher...0m
[16:10:03] 🎉 Done matching COLMAP features.                                                         

0

In [6]:
# run the model
model = "nerfacto"
os.system(f"ns-train {model} --viewer.websocket-port 7007 --viewer.make-share-url True nerfstudio-data --data {processed_data_path} --downscale-factor 4")

──────────────────────────────────────────────────────── Config ────────────────────────────────────────────────────────
TrainerConfig(
    _target=<class 'nerfstudio.engine.trainer.Trainer'>,
    output_dir=PosixPath('outputs'),
    method_name='nerfacto',
    experiment_name=None,
    project_name='nerfstudio-project',
    timestamp='2024-12-03_163958',
    machine=MachineConfig(seed=42, num_devices=1, num_machines=1, machine_rank=0, dist_url='auto', device_type='cuda'),
    logging=LoggingConfig(
        relative_log_dir=PosixPath('.'),
        steps_per_log=10,
        max_buffer_size=20,
        local_writer=LocalWriterConfig(
            _target=<class 'nerfstudio.utils.writer.LocalWriter'>,
            enable=True,
            stats_to_track=(
                <EventName.ITER_TRAIN_TIME: 'Train Iter (time)'>,
                <EventName.TRAIN_RAYS_PER_SEC: 'Train Rays / Sec'>,
                <EventName.CURR_TEST_PSNR: 'Test PSNR'>,
                <EventName.VIS_RAYS_PER_SEC: 'Vi